In [108]:
import numpy as np
import matplotlib.pyplot as plt
import math
import random

import wave
from IPython.display import display, Audio
%matplotlib inline

In [109]:
def loadfile():
    f1 = wave.open(r"music1.wav","rb")
    f2 = wave.open(r"music2.wav","rb")
    
    params1 = f1.getparams()
    nchannels1, sampwidth1, framerate1, nframes1 = params1[:4]
    params2 = f2.getparams()
    nchannels2, sampwidth2, framerate2, nframes2 = params2[:4]
    
    dat1 = f1.readframes(nframes1)
    dat2 = f2.readframes(nframes2)
    
    f1.close()
    f2.close()
    
    a = np.fromstring(dat1,dtype = np.int16)
    b = np.fromstring(dat2,dtype = np.int16) 
    n = np.shape(a)
    c = np.array([a, b])
    return c,n

In [110]:
def white(x):
    s = np.shape(x)
    mean = x.mean(axis=-1)
    for i in range(s[0]):
        for j in range(s[1]):
            x[i][j] = x[i][j] - mean[i]
    sig = np.dot(x, x.T)
    D,E = np.linalg.eig(sig)
    n = np.shape(D)
    for i in range(s[0]):
        D[i] = math.sqrt(D[i])
    d = np.diag(1/D)
    V = np.dot(d, E.T)
    z = np.dot(V, x)
    return z

In [111]:
print("music1:")
display(Audio(x[0], rate=44100))

music1:


In [112]:
print("music2:")
display(Audio(x[1], rate=44100))

music2:


In [113]:
x,n = loadfile()
z = Whitening(x)

In [121]:
def Decorrelation(W):
    D, E = np.linalg.eigh(np.dot(W, W.T))
    return np.dot(np.dot(E * (1. / np.sqrt(D)), E.T), W)

In [157]:
#To Aliceを分ける最適なWの初期値
import random
def gradient(z):
    s = np.shape(z)
    m = s[0]
    W = np.random.rand(m, m)
    W[0][0] = 0.63017188
    W[0][1] = 0.48873888
    W[1][0] = 0.07891237
    W[1][1] = 0.67492541
    print("ランダムに生成するWは以下です：")
    print(W)
    lim = 200
    for j in range(200):
        W1 = W
        W = W/np.linalg.norm(W)
        y = np.dot(W.T,z)
        W = (z * pow(y,3)).mean(axis=-1) - 3*W
        W = W/np.linalg.norm(W)
        W = Decorrelation(W)
        lim = max( abs(abs(np.diag(np.dot(W, W1.T))) - 1))
        if lim < 0.00000001:
            break
            
    return W
#Turkishを分ける最適なWの初期値は
#[[ 0.45987049  0.29996253] [ 0.2286032   0.18762922]]

In [158]:
W = gradient(z)
print("収束して得たWは以下です：")
print(W)

ランダムに生成するWは以下です：
[[ 0.63017188  0.48873888]
 [ 0.07891237  0.67492541]]
収束して得たWは以下です：
[[ 0.91862043+0.j  0.39514113+0.j]
 [-0.39514113+0.j  0.91862043+0.j]]


In [159]:
y = np.dot(W,z)

In [160]:
print("source1:")
display(Audio(y[0], rate=44100))

source1:


/usr/local/brew/opt/pyenv/versions/anaconda3-4.4.0/lib/python3.6/site-packages/IPython/lib/display.py:123: ComplexWarning: Casting complex values to real discards the imaginary part
  data = np.array(data, dtype=float)


In [161]:
print("source2:")
display(Audio(y[1], rate=44100))

source2:


/usr/local/brew/opt/pyenv/versions/anaconda3-4.4.0/lib/python3.6/site-packages/IPython/lib/display.py:123: ComplexWarning: Casting complex values to real discards the imaginary part
  data = np.array(data, dtype=float)
